In [1]:
from bnlp import POS
from tqdm import tqdm

In [2]:
def load_data(filename):
    with open(filename, 'r',encoding='utf-8') as f:
        data = [line.strip().split(' _ _ ') for line in f.readlines()]
        # return data
        # empty lines are used to separate sentences
        # separate them into sentences
        sentences = []
        cur = []
        for line in data:
            if line == ['']:
                cur = [tuple(line) for line in cur]
                sentences.append(cur)
                cur = []
            else:
                # for p in punctuations:
                #     line[0] = line[0].replace(p, '')
                if len(line[0]) == 0:
                    line[0] = ' '
                cur.append(line)
        # # convert each list to a tuple
        sentences.append(cur)
        return sentences
    
dev = load_data('dev.txt')
bn_pos = POS()
model_path = "bnlp/model/bn_pos.pkl"

def add_pos(sentence):
    # first one of the tuple is the word and the second one is the ner  
    words = []
    for word in sentence:
        words.append(word[0])
    pos = bn_pos.tag(model_path, words)
    ## add ner back to the tuple
    ret = []
    for i in range(len(pos)):
        word = sentence[i][0]
        ner = sentence[i][1]
        ret.append((word, pos[i][1], ner))
    return ret

def add_pos_to_all(sents):
    ret = []
    for i in tqdm(range(len(sents))):
        # if i % 1000 == 0:
        #     print(i)
        ret.append(add_pos(sents[i]))
    return ret

dev_sents = add_pos_to_all(dev)

100%|██████████| 801/801 [00:06<00:00, 124.89it/s]


In [3]:
dev_sents.pop()

[]

In [4]:
import pickle
import numpy
from bnlp import POS
from tqdm import tqdm
import nltk
import sklearn
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.preprocessing import LabelBinarizer
import sklearn_crfsuite as crfsuite
from sklearn_crfsuite import metrics
import string

In [5]:
import pickle

In [6]:
with open('train_sents.pickle', 'rb') as handle:
    train_sents = pickle.load(handle)

# with open('dev_sents.pickle', 'rb') as handle:
    # dev_sents = pickle.load(handle)

with open('test_main_sents.pickle', 'rb') as handle:
    test_sents = pickle.load(handle)

In [7]:
len(test_sents.pop())

0

In [8]:
len(train_sents.pop())

0

In [9]:
# word frequency information

def get_all_words(sents):
    words = []
    for i in range(len(sents)):
        for w in sents[i]:
            words += [w[0]]
    return words

all_train_words = get_all_words(train_sents)
len(all_train_words)

word_freq = {}
for w in all_train_words:
    if w in word_freq:
        word_freq[w] += 1
    else:
        word_freq[w] = 1

In [10]:
# Gazzeter Implementation

GRP_bn = {}
LOC_bn = {}
PER_bn = {}
PROD_bn = {}
CORP_bn = {}
CW_bn = {}


with open('gazz_main/CORP.txt') as file:
    lines = [x.strip() for x in file.readlines()]
    for l in lines:
        CORP_bn[l] = 1
        words = l.split()
        for size in range(2, 4, 1):
            for i in range(len(words)):
                if (i + size) >= len(words):
                    break
                CORP_bn[" ".join(words[i: i+size])] = 1

with open('gazz_main/CW.txt') as file:
    lines = [x.strip() for x in file.readlines()]
    for l in lines:
        CW_bn[l] = 1
        words = l.split()
        for size in range(2, 4, 1):
            for i in range(len(words)):
                if (i + size) >= len(words):
                    break
                CW_bn[" ".join(words[i: i+size])] = 1

with open('gazz_main/GRP.txt') as file:
    lines = [x.strip() for x in file.readlines()]
    for l in lines:
        GRP_bn[l] = 1
        words = l.split()
        for size in range(2, 4, 1):
            for i in range(len(words)):
                if (i + size) >= len(words):
                    break
                GRP_bn[" ".join(words[i: i+size])] = 1


with open('gazz_main/LOC.txt') as file:
    lines = [x.strip() for x in file.readlines()]
    for l in lines:
        LOC_bn[l] = 1
        words = l.split()
        for size in range(2, 4, 1):
            for i in range(len(words)):
                if (i + size) >= len(words):
                    break
                LOC_bn[" ".join(words[i: i+size])] = 1

with open('gazz_main/PER.txt') as file:
    lines = [x.strip() for x in file.readlines()]
    for l in lines:
        PER_bn[l] = 1
        words = l.split()
        for size in range(2, 4, 1):
            for i in range(len(words)):
                if (i + size) >= len(words):
                    break
                PER_bn[" ".join(words[i: i+size])] = 1


with open('gazz_main/PROD.txt') as file:
    lines = [x.strip() for x in file.readlines()]
    for l in lines:
        PROD_bn[l] = 1
        words = l.split()
        for size in range(2, 4, 1):
            for i in range(len(words)):
                if (i + size) >= len(words):
                    break
                PROD_bn[" ".join(words[i: i+size])] = 1

In [11]:
def extract_sentences_from_file(file_name):
    sentences = []
    current_sentence = ""

    with open(file_name, "r", encoding="utf-8") as file:
        for line in tqdm(file):
            line = line.strip()
            if line:
                if current_sentence:
                    current_sentence += " "
                current_sentence += line.split()[0]
            else:
                if current_sentence:
                    sentences.append(current_sentence)
                    current_sentence = ""

    if current_sentence:
        sentences.append(current_sentence)

    return sentences


# Example usage
dev_lines = extract_sentences_from_file('dev.txt')
test_lines = extract_sentences_from_file('test.txt')
train_lines = extract_sentences_from_file('train.txt')

11131it [00:00, 1309367.23it/s]
826917it [00:00, 1671982.91it/s]
207127it [00:00, 1562953.44it/s]


In [12]:
# BanglaBert Feature Extraction

import torch
from transformers import ElectraTokenizer, ElectraForTokenClassification, AutoConfig
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

cache_dir = "cache"
model_name_or_path = "checkpoint-7500"
config = AutoConfig.from_pretrained(
    model_name_or_path,
    cache_dir=cache_dir,
    output_hidden_states = True
)   

tokenizer = ElectraTokenizer.from_pretrained(
    model_name_or_path,
)

model = ElectraForTokenClassification.from_pretrained(
    model_name_or_path,
    config=config,
    cache_dir=cache_dir,
)

def concat_hidden_states(text):
    temp = ''
    for i in text:
        if i not in string.punctuation:
            temp+=i


    text = tokenizer(temp)
    input_ids = torch.tensor(text['input_ids']).unsqueeze(0)  # Convert to tensor and add batch dimension
    words = tokenizer.convert_ids_to_tokens(input_ids[0])
    # print(words)
    attention_mask = torch.tensor(text['attention_mask']).unsqueeze(0)  # Convert to tensor and add batch dimension

    outputs = model(input_ids=input_ids, attention_mask=attention_mask)
    hidden_states = outputs.hidden_states

    # layer1 = hidden_states[0]
    # layer2 = hidden_states[1]
    # layer3 = hidden_states[2]
    # layer4 = hidden_states[3]
    # layer5 = hidden_states[4]
    # layer6 = hidden_states[5]
    # layer7 = hidden_states[6]
    # layer8 = hidden_states[7]
    # layer9 = hidden_states[8]
    # layer10 = hidden_states[9]
    # layer11 = hidden_states[10]
    # layer12 = hidden_states[11]
    # layer13 = hidden_states[12]
    # layer14 = hidden_states[13]
    # layer15 = hidden_states[14]
    # layer16 = hidden_states[15]
    # layer17 = hidden_states[16]
    # layer18 = hidden_states[17]
    # layer19 = hidden_states[18]
    # layer20 = hidden_states[19]
    # layer21 = hidden_states[20]
    # layer22 = hidden_states[21]
    # layer23 = hidden_states[22]
    layer24 = hidden_states[23]

    # hidden = [layer1, layer2, layer3, layer4, layer5, 
    #           layer6, layer7, layer8, layer9, layer10, 
    #           layer11, layer12, layer13, layer14, layer15, 
    #           layer16, layer17, layer18, layer19, layer20, 
    #           layer21, layer22, layer23, layer24]

    hidden = [layer24]
    
    concatenated_tensor = torch.cat(hidden, dim=2)

    # averaged_hidden_states = torch.mean(torch.stack(hidden), dim=0)
    concatenated_tensor = concatenated_tensor.detach().numpy()
    
    new_concatenated_tensor = []

    count = 0
    for i in concatenated_tensor[0]:
        if (words[count].startswith('#') or words[count] in ['[CLS]','[SEP]'])  == False:
            new_concatenated_tensor.append(i)
        count+=1
        
    return numpy.asarray(new_concatenated_tensor)

c:\Users\User\anaconda3\envs\gputorch\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [13]:
len(train_sents)

15300

In [14]:
with open('kmodel_main_23_layer.pickle', 'rb') as handle:
    kmodel = pickle.load(handle)

In [15]:
len(test_sents)

133119

In [16]:
import string
punctuation = string.punctuation + '।'
def ispunct(word):
    word = word.strip()
    if len(word) == 1 and any(char in punctuation for char in word):
        return 1
    else:
        return 0

In [17]:
global_count = 0

In [18]:
import string
punctuation = string.punctuation + '।'

def ispunct(word):
    word = word.strip()
    if len(word) == 1 and any(char in punctuation for char in word):
        return 1
    else:
        return 0

ispunct("; ")

1

In [19]:
st = ["অতএব","অথচ","অথবা","অনুযায়ী","অনেক","অনেকে","অনেকেই","অন্তত","অন্য","অবধি","অবশ্য","অর্থাত","আই","আগামী","আগে","আগেই","আছে","আজ","আদ্যভাগে","আপনার","আপনি","আবার","আমরা","আমাকে","আমাদের","আমার","আমি","আর","আরও","ই","ইত্যাদি","ইহা","উচিত","উত্তর","উনি","উপর","উপরে","এ","এঁদের","এঁরা","এই","একই","একটি","একবার","একে","এক্","এখন","এখনও","এখানে","এখানেই","এটা","এটাই","এটি","এত","এতটাই","এতে","এদের","এব","এবং","এবার","এমন","এমনকী","এমনি","এর","এরা","এল","এস","এসে","ঐ","ও","ওঁদের","ওঁর","ওঁরা","ওই","ওকে","ওখানে","ওদের","ওর","ওরা","কখনও","কত","কবে","কমনে","কয়েক","কয়েকটি","করছে","করছেন","করতে","করবে","করবেন","করলে","করলেন","করা","করাই","করায়","করার","করি","করিতে","করিয়া","করিয়ে","করে","করেই","করেছিলেন","করেছে","করেছেন","করেন","কাউকে","কাছ","কাছে","কাজ","কাজে","কারও","কারণ","কি","কিংবা","কিছু","কিছুই","কিন্তু","কী","কে","কেউ","কেউই","কেখা","কেন","কোটি","কোন","কোনও","কোনো","ক্ষেত্রে","কয়েক","খুব","গিয়ে","গিয়েছে","গিয়ে","গুলি","গেছে","গেল","গেলে","গোটা","চলে","চান","চায়","চার","চালু","চেয়ে","চেষ্টা","ছাড়া","ছাড়াও","ছিল","ছিলেন","জন","জনকে","জনের","জন্য","জন্যওজে","জানতে","জানা","জানানো","জানায়","জানিয়ে","জানিয়েছে","জে","জ্নজন","টি","ঠিক","তখন","তত","তথা","তবু","তবে","তা","তাঁকে","তাঁদের","তাঁর","তাঁরা","তাঁাহারা","তাই","তাও","তাকে","তাতে","তাদের","তার","তারপর","তারা","তারৈ","তাহলে","তাহা","তাহাতে","তাহার","তিনঐ","তিনি","তিনিও","তুমি","তুলে","তেমন","তো","তোমার","থাকবে","থাকবেন","থাকা","থাকায়","থাকে","থাকেন","থেকে","থেকেই","থেকেও","দিকে","দিতে","দিন","দিয়ে","দিয়েছে","দিয়েছেন","দিলেন","দু","দুই","দুটি","দুটো","দেওয়া","দেওয়ার","দেওয়া","দেখতে","দেখা","দেখে","দেন","দেয়","দ্বারা","ধরা","ধরে","ধামার","নতুন","নয়","না","নাই","নাকি","নাগাদ","নানা","নিজে","নিজেই","নিজেদের","নিজের","নিতে","নিয়ে","নিয়ে","নেই","নেওয়া","নেওয়ার","নেওয়া","নয়","পক্ষে","পর","পরে","পরেই","পরেও","পর্যন্ত","পাওয়া","পাচ","পারি","পারে","পারেন","পি","পেয়ে","পেয়্র্","প্রতি","প্রথম","প্রভৃতি","প্রযন্ত","প্রাথমিক","প্রায়","প্রায়","ফলে","ফিরে","ফের","বক্তব্য","বদলে","বন","বরং","বলতে","বলল","বললেন","বলা","বলে","বলেছেন","বলেন","বসে","বহু","বা","বাদে","বার","বি","বিনা","বিভিন্ন","বিশেষ","বিষয়টি","বেশ","বেশি","ব্যবহার","ব্যাপারে","ভাবে","ভাবেই","মতো","মতোই","মধ্যভাগে","মধ্যে","মধ্যেই","মধ্যেও","মনে","মাত্র","মাধ্যমে","মোট","মোটেই","যখন","যত","যতটা","যথেষ্ট","যদি","যদিও","যা","যাঁর","যাঁরা","যাওয়া","যাওয়ার","যাওয়া","যাকে","যাচ্ছে","যাতে","যাদের","যান","যাবে","যায়","যার","যারা","যিনি","যে","যেখানে","যেতে","যেন","যেমন","র","রকম","রয়েছে","রাখা","রেখে","লক্ষ","শুধু","শুরু","সঙ্গে","সঙ্গেও","সব","সবার","সমস্ত","সম্প্রতি","সহ","সহিত","সাধারণ","সামনে","সি","সুতরাং","সে","সেই","সেখান","সেখানে","সেটা","সেটাই","সেটাও","সেটি","স্পষ্ট","স্বয়ং","হইতে","হইবে","হইয়া","হওয়া","হওয়ায়","হওয়ার","হচ্ছে","হত","হতে","হতেই","হন","হবে","হবেন","হয়","হয়তো","হয়নি","হয়ে","হয়েই","হয়েছিল","হয়েছে","হয়েছেন","হল","হলে","হলেই","হলেও","হলো","হাজার","হিসাবে","হৈলে","হোক","হয়"]
def isStopword(word):
    if word in st:
        return 1
    else: return 0

isStopword('অনেক')

1

In [20]:
def isBangla(word):
    for char in word:
        if (2432 <= ord(char) <= 2559) or (ord(char) == 32) or (char in ["।"]):
            return 1
    return 0

In [21]:
# x = concat_hidden_states('অথচ অনুযায়ী')
# for i in x:
#     for j in i:
#         print(int(j*100))

In [22]:
# for dev
#
def wordToFeatures(sent, bert_emb, idx):
    word = sent[idx][0]
    postag = sent[idx][1]

    try:
        bert_cluster = kmodel.predict([bert_emb[idx]])[0]
    except:
        bert_cluster = -1

    features = {
        'bias': 1.0,
        'word': word,
        'bert': bert_cluster,
        'word[-3:]': word[-3:],
        'word[-2:]': word[-2:],
        'word[-1:]': word[-1:],
        'word[:3]': word[:3],
        'word[:2]': word[:2],
        'word[:1]': word[:1],
        'word.isdigit': word.isdigit(),
        'word.ispunctuation': ispunct(word),
        'word.isBangla': isBangla(word),
        'word.isStopword': isStopword(word),
        'index': idx,
        'length': len(word),
        'postag': postag,
        'freq': word_freq[word] if word in word_freq else 0,
        'is_corp': int(word in CORP_bn), 
        'is_cw': int(word in CW_bn), 
        'is_grp': int(word in GRP_bn), 
        'is_loc': int(word in LOC_bn), 
        'is_per': int(word in PER_bn), 
        'is_prod': int(word in PROD_bn),
    }
    
    try:
        for iv, value in enumerate(bert_emb[idx]):
            features['bert_emb{}'.format(iv)] = int(value*100)
    except:
        features['bert_emb'] = 'error'

    if idx > 0:
        sub = sent[idx-1][0] + " "+ sent[idx][0]
        if sub in CORP_bn:
            features['is_corp'] = 2
        if sub in CW_bn:
            features['is_cw'] = 2
        if sub in GRP_bn:
            features['is_grp'] = 2
        if sub in LOC_bn:
            features['is_loc'] = 2
        if sub in PER_bn:
            features['is_per'] = 2
        if sub in PROD_bn:
            features['is_prod'] = 2
    
    if idx < len(sent) - 1:
        sub = sent[idx][0] + " "+ sent[idx+1][0]
        if sub in CORP_bn:
            features['is_corp'] = 2
        if sub in CW_bn:
            features['is_cw'] = 2
        if sub in GRP_bn:
            features['is_grp'] = 2
        if sub in LOC_bn:
            features['is_loc'] = 2
        if sub in PER_bn:
            features['is_per'] = 2
        if sub in PROD_bn:
            features['is_prod'] = 2
    
    if idx > 1:
        sub = sent[idx-2][0] + " "+ sent[idx-1][0] + " " + sent[idx][0]
        if sub in CORP_bn:
            features['is_corp'] = 3
        if sub in CW_bn:
            features['is_cw'] = 3
        if sub in GRP_bn:
            features['is_grp'] = 3
        if sub in LOC_bn:
            features['is_loc'] = 3
        if sub in PER_bn:
            features['is_per'] = 3
        if sub in PROD_bn:
            features['is_prod'] = 3
    if idx < len(sent) - 2:
        sub = sent[idx][0] + " "+ sent[idx+1][0] + " " + sent[idx+2][0]
        if sub in CORP_bn:
            features['is_corp'] = 3
        if sub in CW_bn:
            features['is_cw'] = 3
        if sub in GRP_bn:
            features['is_grp'] = 3
        if sub in LOC_bn:
            features['is_loc'] = 3
        if sub in PER_bn:
            features['is_per'] = 3
        if sub in PROD_bn:
            features['is_prod'] = 3
        
    
    for i in range(1, 3):
        if idx < i:
            break
        wordi = sent[idx-i][0]
        postagi = sent[idx-i][1]

        try:
            bert_cluster = kmodel.predict([bert_emb[idx-i]])[0]
        except:
            bert_cluster = -1

        features.update({
            '-{}:word'.format(i): wordi,
            '-{}:bert'.format(i): bert_cluster,
            '-{}:word[-3:]'.format(i): wordi[-3:],
            '-{}:word[-2:]'.format(i): wordi[-2:],
            '-{}:word[-1:]'.format(i): wordi[-1:],
            '-{}:word[:3]'.format(i): wordi[:3],
            '-{}:word[:2]'.format(i): wordi[:2],
            '-{}:word[:1]'.format(i): wordi[:1],
            '-{}:length'.format(i): len(wordi),
            '-{}:word.isdigit'.format(i): wordi.isdigit(),
            '-{}:word.isBangla'.format(i): isBangla(wordi),
            '-{}:word.isBangla'.format(i): isBangla(wordi),
            '-{}:word.isStopword'.format(i): isStopword(wordi),
            '-{}:postag'.format(i): postagi,
            '-{}:is_corp'.format(i): int(wordi in CORP_bn), 
            '-{}:is_cw'.format(i): int(wordi in CW_bn), 
            '-{}:is_grp'.format(i): int(wordi in GRP_bn), 
            '-{}:is_loc'.format(i): int(wordi in LOC_bn), 
            '-{}:is_per'.format(i): int(wordi in PER_bn), 
            '-{}:is_prod'.format(i): int(wordi in PROD_bn),
        })
        # try:
        #     for iv, value in enumerate(bert_emb[idx-i]):
        #         features['-{}:bert_emb{}'.format(i,iv)] = int(value*100)
        # except:
        #     features['{}:bert_emb'.format(i)] = 'error'
    
    for i in range(1, 3):
        if (idx+i) >= len(sent):
            break
        wordi = sent[idx+i][0]
        postagi = sent[idx+i][1]
        
        try:
            bert_cluster = kmodel.predict([bert_emb[idx+i]])[0]
        except:
            bert_cluster = -1

        features.update({
            '{}:word'.format(i): wordi,
            '{}:bert'.format(i): bert_cluster,
            '{}:word[-3:]'.format(i): wordi[-3:],
            '{}:word[-2:]'.format(i): wordi[-2:],
            '{}:word[-1:]'.format(i): wordi[-1:],
            '{}:word[:3]'.format(i): wordi[:3],
            '{}:word[:2]'.format(i): wordi[:2],
            '{}:word[:1]'.format(i): wordi[:1],
            '{}:length'.format(i): len(wordi),
            '{}:word.isdigit'.format(i): wordi.isdigit(),
            '{}:word.ispunctuation'.format(i): ispunct(wordi),
            '{}:word.isBangla'.format(i): isBangla(wordi),
            '{}:word.isStopword'.format(i): isStopword(wordi),
            '{}:postag'.format(i): postagi,
            '{}:is_corp'.format(i): int(wordi in CORP_bn), 
            '{}:is_cw'.format(i): int(wordi in CW_bn), 
            '{}:is_grp'.format(i): int(wordi in GRP_bn), 
            '{}:is_loc'.format(i): int(wordi in LOC_bn), 
            '{}:is_per'.format(i): int(wordi in PER_bn), 
            '{}:is_prod'.format(i): int(wordi in PROD_bn),
        })
        # print(bert_emb.shape, idx+i)
        # try:
        #     for iv, value in enumerate(bert_emb[idx+i]):
        #         features['{}:bert_emb{}'.format(i, iv)] = int(value*100)
        # except:
        #     features['{}:bert_emb'.format(i)] = 'error'
        
    if idx == 0:
        features['BOS'] = True
    if idx == len(sent) - 1:
        features['EOS'] = True
    
    return features

def sentTofeatures(sent):
    global global_count
    sentence = test_lines[global_count]
    bert_word_embeddings = concat_hidden_states(sentence)
    # if global_count % 500:
    #     print(global_count, end = " -> ") 
    x = [wordToFeatures(sent, bert_word_embeddings, i) for i in range(len(sent))]
    global_count+=1
    return x

def sentTolabels(sent):
    return [label for token, postag, label in sent]

In [23]:
global_count = 0

In [28]:
X_train = [sentTofeatures(s) for s in tqdm(train_sents)]
y_train = [sentTolabels(s) for s in train_sents]

100%|██████████| 15300/15300 [1:31:16<00:00,  2.79it/s]


In [30]:
with open('allfeatures_X_train.pickle', 'wb') as handle:
    pickle.dump(X_train, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('allfeatures_y_train.pickle', 'wb') as handle:
    pickle.dump(y_train, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [35]:
X_dev = [sentTofeatures(s) for s in tqdm(dev_sents)]
y_dev = [sentTolabels(s) for s in dev_sents]

100%|██████████| 800/800 [06:18<00:00,  2.11it/s]


In [39]:
with open('allfeatures_X_dev.pickle', 'wb') as handle:
    pickle.dump(X_dev, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('allfeatures_y_dev.pickle', 'wb') as handle:
    pickle.dump(y_dev, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [24]:
del train_sents

In [25]:
len(test_sents[:20000])

20000

In [47]:
%%time
X_test = [sentTofeatures(s) for s in tqdm(test_sents[:20000])]
y_test = [sentTolabels(s) for s in test_sents]

100%|██████████| 20000/20000 [59:15<00:00,  5.63it/s] 


CPU times: total: 7h 52min 57s
Wall time: 59min 15s


In [50]:
y_test = [sentTolabels(s) for s in test_sents[:20000]]
y_pred = crf.predict(X_test)
metrics.flat_f1_score(y_test, y_pred,
                      average='macro', labels=labels)

0.7363789904764386

In [29]:
global_count = 20000

In [32]:
# del X_test
X_test = [sentTofeatures(s) for s in tqdm(test_sents[20000:60000])]
y_test = [sentTolabels(s) for s in test_sents[20000:60000]]

y_pred = crf.predict(X_test)
metrics.flat_f1_score(y_test, y_pred,
                      average='macro', labels=labels)

  8%|▊         | 3018/40000 [07:31<1:47:56,  5.71it/s]

In [ ]:
del X_test
X_test = [sentTofeatures(s) for s in tqdm(test_sents[60000:100000])]
y_test = [sentTolabels(s) for s in test_sents[60000:100000]]

y_pred = crf.predict(X_test)
metrics.flat_f1_score(y_test, y_pred,
                      average='macro', labels=labels)

In [ ]:
del X_test
X_test = [sentTofeatures(s) for s in tqdm(test_sents[100000:])]
y_test = [sentTolabels(s) for s in test_sents[100000:]]

y_pred = crf.predict(X_test)
metrics.flat_f1_score(y_test, y_pred,
                      average='macro', labels=labels)

In [ ]:
global_count

In [43]:
# with open('veryImportantX_test', 'wb') as handle:
#     pickle.dump(X_test, handle, protocol=pickle.HIGHEST_PROTOCOL)
# with open('veryImportanty_test', 'wb') as handle:
#     pickle.dump(y_test, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [31]:
crf = crfsuite.CRF(
    verbose='true',
    algorithm='lbfgs',
    c1=0.1,
    c2=0.1,
    max_iterations=150,
    all_possible_transitions=True
)

try:
    crf.fit(X_train, y_train)
except:
    pass

loading training data to CRFsuite: 100%|██████████| 15300/15300 [01:09<00:00, 219.63it/s]



Feature generation
type: CRF1d
feature.minfreq: 0.000000
feature.possible_states: 0
feature.possible_transitions: 1
0....1....2....3....4....5....6....7....8....9....10
Number of features: 411400
Seconds required: 12.709

L-BFGS optimization
c1: 0.100000
c2: 0.100000
num_memories: 6
max_iterations: 150
epsilon: 0.000010
stop: 10
delta: 0.000010
linesearch: MoreThuente
linesearch.max_iterations: 20

Iter 1   time=51.22 loss=299702.12 active=405070 feature_norm=0.02
Iter 2   time=6.39  loss=210504.39 active=372127 feature_norm=0.02
Iter 3   time=6.39  loss=39190.93 active=206090 feature_norm=0.02
Iter 4   time=6.42  loss=32347.02 active=258481 feature_norm=0.02
Iter 5   time=6.39  loss=30969.47 active=246933 feature_norm=0.02
Iter 6   time=6.39  loss=29081.47 active=230022 feature_norm=0.02
Iter 7   time=6.40  loss=24276.57 active=202698 feature_norm=0.02
Iter 8   time=12.82 loss=17082.23 active=151851 feature_norm=0.02
Iter 9   time=19.40 loss=15586.80 active=145623 feature_norm=0.02
I

In [32]:
with open('crf_allfeatures.pickle', 'wb') as handle:
    pickle.dump(crf, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [30]:
with open('crf_allfeatures.pickle', 'rb') as handle:
    crf = pickle.load(handle)

In [31]:
labels = list(crf.classes_)
labels

['O',
 'B-CORP',
 'B-GRP',
 'I-GRP',
 'B-PER',
 'I-PER',
 'I-CORP',
 'B-CW',
 'I-CW',
 'B-PROD',
 'I-PROD',
 'B-LOC',
 'I-LOC']

In [37]:
y_pred = crf.predict(X_dev)
metrics.flat_f1_score(y_dev, y_pred,
                      average='macro', labels=labels)

                      ### f1 accuracy komse 0.80527719

0.841622238522134

In [89]:
from collections import Counter

def print_transitions(trans_features):
    for (label_from, label_to), weight in trans_features:
        print("%-6s -> %-7s %0.6f" % (label_from, label_to, weight))

print("Top likely transitions:")
print_transitions(Counter(crf.transition_features_).most_common(100))

print("\nTop unlikely transitions:")
print_transitions(Counter(crf.transition_features_).most_common()[-20:])

Top likely transitions:
B-PER  -> I-PER   6.263656
B-CW   -> I-CW    4.440877
B-LOC  -> I-LOC   4.227208
B-PROD -> I-PROD  3.868802
B-GRP  -> I-GRP   3.700964
I-LOC  -> I-LOC   3.683053
B-CORP -> I-CORP  3.658995
I-CW   -> I-CW    3.402395
I-GRP  -> I-GRP   3.347307
I-CORP -> I-CORP  3.265143
I-PER  -> I-PER   2.520600
I-PROD -> I-PROD  2.438461
O      -> O       2.057119
O      -> B-CORP  1.065418
O      -> B-LOC   1.027370
O      -> B-PROD  0.663818
O      -> B-GRP   0.581994
O      -> B-PER   0.407113
B-CW   -> O       0.075750
I-PER  -> O       0.000386
O      -> B-CW    0.000318
I-LOC  -> O       -0.000314
I-PROD -> O       -0.001235
B-LOC  -> O       -0.004118
I-CORP -> O       -0.006468
I-CW   -> O       -0.079881
I-GRP  -> O       -0.090282
B-PROD -> O       -0.099031
B-CORP -> O       -0.488577
B-PER  -> O       -0.841377
I-PROD -> B-CORP  -1.034548
I-LOC  -> B-PROD  -1.050150
I-PROD -> B-LOC   -1.058766
I-LOC  -> B-PER   -1.173520
I-PROD -> B-GRP   -1.182246
B-GRP  -> O      

In [96]:
def print_state_features(state_features):
    for (attr, label), weight in state_features:
        print("%0.6f %-8s %s" % (weight, label, attr))    

print("Top positive:")
print_state_features(Counter(crf.state_features_).most_common(100000))

print("\nTop negative:")
print_state_features(Counter(crf.state_features_).most_common()[-30:])

Top positive:
5.051976 O        BOS
4.132936 O        word.ispunctuation
4.129675 O        word[:2]:(১
3.883161 B-LOC    is_loc
3.815410 B-PROD   is_prod
3.655832 O        word[-3:]:ুলি
3.499220 O        word[-2:]:ে,
3.158224 O        EOS
3.137610 O        word[-2:]:েও
3.088353 O        word[:2]:১৯
3.016768 O        word[-2:]:তে
2.908136 B-CORP   is_corp
2.761529 O        word[-2:]:ে।
2.747768 O        1:word[:3]:করে
2.728286 B-CW     word:আইটিউন্স
2.705273 B-PER    is_per
2.685630 O        word[:3]:বেশ
2.676881 O        word[-2:]:কে
2.670684 B-CORP   word:ভ্যারাইটি
2.619901 O        word[-2:]:ের
2.586866 O        word[-2:]:া,
2.583582 O        word[-2:]:টে
2.539503 B-CW     word:চিত্রসংগীত
2.531879 B-CW     word:সুপারটেড
2.517251 B-CORP   word[-2:]:এন
2.502669 I-GRP    word:বিশ্ববিদ্যালয়
2.458823 B-CW     word:উপাখ্যান
2.290775 B-PROD   word:ডিভিডি
2.284806 O        word[-2:]:ি,
2.274959 O        word[-2:]:মে
2.262092 O        word[-2:]:ন।
2.261025 O        word[-2:]:ক,
2.255258 O   